In [2]:
import os
from huggingface_hub import login

HF_TOKEN = open("/home/IITB/ai-at-ieor/23m1521/.cache/huggingface/token", "r").read().strip()
os.environ["HF_TOKEN"] = HF_TOKEN
login(token=HF_TOKEN)

Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


In [1]:
import polars as pl

df2 = pl.scan_parquet('hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Anantpur/train-*.parquet')
df2

In [2]:
df2 = df2.with_columns(
	pl.col('audio').struct.field('path').alias('audio_path')
).drop('audio')
df2

In [3]:
df2.columns

/tmp/ipykernel_2159560/3936327964.py:1: PerformanceWarning: Determining the column names of a LazyFrame requires resolving its schema, which is a potentially expensive operation. Use `LazyFrame.collect_schema().names()` to get the column names without this warning.
  df2.columns


['language',
 'languagesKnown',
 'gender',
 'state',
 'district',
 'pincode',
 'stay(years)',
 'isTranscriptionAvailable',
 'transcript',
 'referenceImage',
 'audio_path']

In [4]:
df2.select(pl.col('isTranscriptionAvailable').value_counts()).collect()

shape: (2, 1)
┌──────────────────────────┐
│ isTranscriptionAvailable │
│ ---                      │
│ struct[2]                │
╞══════════════════════════╡
│ {"No",113132}            │
│ {"Yes",5420}             │
└──────────────────────────┘

In [6]:
df2.collect().write_parquet("AndhraPradesh_Anantpur_meta.parquet", compression="gzip")

In [ ]:
import polars as pl

df = pl.read_parquet('hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Anantpur/train-*.parquet')
df

In [7]:
import os
from huggingface_hub import login

HF_TOKEN = open("/home/IITB/ai-at-ieor/23m1521/.cache/huggingface/token", "r").read().strip()
os.environ["HF_TOKEN"] = HF_TOKEN
login(token=HF_TOKEN)

import dask.dataframe as dd

df = dd.read_parquet("hf://datasets/ARTPARK-IISc/Vaani/audio/Delhi/NewDelhi/train-*.parquet")
df                    

Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


Dask DataFrame Structure:
                 audio language languagesKnown  gender   state district pincode stay(years) isTranscriptionAvailable transcript referenceImage
npartitions=54                                                                                                                                
                object   string         string  string  string   string   int64      string                   string     string         string
                   ...      ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...
...                ...      ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...
                   ...      ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...
                   ...      ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...
Dask Name: read_parquet, 1 expression
Expr=ReadParquetFSSpec(446f636)

In [9]:
df['audio_path'] = df['audio'].map(lambda x: x.get('path') if isinstance(x, dict) else None, meta=('audio_path', 'object'))

# Drop the original 'audio' column
df = df.drop(columns='audio')
df

Dask DataFrame Structure:
               language languagesKnown  gender   state district pincode stay(years) isTranscriptionAvailable transcript referenceImage audio_path
npartitions=54                                                                                                                                   
                 string         string  string  string   string   int64      string                   string     string         string     object
                    ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...        ...
...                 ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...        ...
                    ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...        ...
                    ...            ...     ...     ...      ...     ...         ...                      ...        ...            ...        ...
Dask Name: drop_by_shallow_copy, 5 expressions
Expr=Drop(frame=Assign(frame=ReadParquetFSSpec(446f636)), columns='audio')

In [10]:
savedir = "/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData"
state = 'Delhi'
district = 'NewDelhi'
output_path = f"{savedir}/{state}_{district}_meta.parquet"
df.to_parquet(output_path, compression='gzip', engine='pyarrow', write_index=False)

'(ReadTimeoutError("HTTPSConnectionPool(host='cdn-lfs-us-1.hf.co', port=443): Read timed out. (read timeout=10)"), '(Request ID: e0ac54e2-ea47-4a2a-80a4-c54485398fba)')' thrown while requesting GET https://huggingface.co/datasets/ARTPARK-IISc/Vaani/resolve/main/audio/Delhi/NewDelhi/train-00028-of-00054.parquet
Retrying in 1s [Retry 1/5].
'(ReadTimeoutError("HTTPSConnectionPool(host='cdn-lfs-us-1.hf.co', port=443): Read timed out. (read timeout=10)"), '(Request ID: f7da590c-34ef-45f7-a824-ceca80b768ff)')' thrown while requesting GET https://huggingface.co/datasets/ARTPARK-IISc/Vaani/resolve/main/audio/Delhi/NewDelhi/train-00043-of-00054.parquet
Retrying in 1s [Retry 1/5].
'HTTPSConnectionPool(host='cdn-lfs-us-1.hf.co', port=443): Read timed out.' thrown while requesting GET https://huggingface.co/datasets/ARTPARK-IISc/Vaani/resolve/main/audio/Delhi/NewDelhi/train-00003-of-00054.parquet
Retrying in 1s [Retry 1/5].
'HTTPSConnectionPool(host='cdn-lfs-us-1.hf.co', port=443): Read timed out.

KeyboardInterrupt: 

In [31]:
df = df.with_columns(df['audio'].struct.field('path').alias('audio_path')).drop('audio')

In [32]:
df

shape: (118_552, 11)
┌──────────┬────────────┬────────┬────────────┬───┬────────────┬───────────┬───────────┬───────────┐
│ language ┆ languagesK ┆ gender ┆ state      ┆ … ┆ isTranscri ┆ transcrip ┆ reference ┆ audio_pat │
│ ---      ┆ nown       ┆ ---    ┆ ---        ┆   ┆ ptionAvail ┆ t         ┆ Image     ┆ h         │
│ str      ┆ ---        ┆ str    ┆ str        ┆   ┆ able       ┆ ---       ┆ ---       ┆ ---       │
│          ┆ str        ┆        ┆            ┆   ┆ ---        ┆ str       ┆ str       ┆ str       │
│          ┆            ┆        ┆            ┆   ┆ str        ┆           ┆           ┆           │
╞══════════╪════════════╪════════╪════════════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│ Telugu   ┆ ['Telugu', ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ 'English'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_An ┆ M_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ ant…      ┆ tpu…      │
│ Telugu   ┆ ['Telugu', ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ 'English'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_GE ┆ M_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ NER…      ┆ tpu…      │
│ Telugu   ┆ ['Telugu', ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ 'English'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_GE ┆ M_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ NER…      ┆ tpu…      │
│ Telugu   ┆ ['Telugu', ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ 'English'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_GE ┆ M_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ NER…      ┆ tpu…      │
│ Telugu   ┆ ['Telugu', ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ 'English'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_GE ┆ M_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ NER…      ┆ tpu…      │
│ …        ┆ …          ┆ …      ┆ …          ┆ … ┆ …          ┆ …         ┆ …         ┆ …         │
│ Hindi    ┆ ['English' ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ , 'Hindi'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_An ┆ S_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ ant…      ┆ tpu…      │
│ Hindi    ┆ ['English' ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ , 'Hindi'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_An ┆ S_AP_Anan │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ ant…      ┆ tpu…      │
│ Hindi    ┆ ['English' ┆ Female ┆ AndhraPrad ┆ … ┆ No         ┆ null      ┆ Images/II ┆ IISc_Vaan │
│          ┆ , 'Hindi'] ┆        ┆ esh        ┆   ┆            ┆           ┆ Sc_VaaniP ┆ iProject_ │
│          ┆            ┆        ┆            ┆   ┆            ┆           ┆ roject_An ┆ S_AP_Anan │
│          ┆            ┆        ┆      

In [38]:
df['isTranscriptionAvailable'].value_counts()

shape: (2, 2)
┌──────────────────────────┬────────┐
│ isTranscriptionAvailable ┆ count  │
│ ---                      ┆ ---    │
│ str                      ┆ u32    │
╞══════════════════════════╪════════╡
│ Yes                      ┆ 5420   │
│ No                       ┆ 113132 │
└──────────────────────────┴────────┘

In [27]:
df['audio'][0]['path']

'IISc_VaaniProject_M_AP_Anantpur_00014520_1544240000_APATSR_190315_1880_16300.wav'

<hr>
<hr>

In [1]:
import datasets
from datasets import Audio
from datasets import load_dataset
from datasets import get_dataset_config_names
import os
from huggingface_hub import login
HF_TOKEN = open("/home/IITB/ai-at-ieor/23m1521/.cache/huggingface/token", "r").read().strip()
login(token=HF_TOKEN)

In [2]:
district = "Delhi_NewDelhi"
cache_dir = f'/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/Audio-Cache/Hindi/{district}'


ds = load_dataset("ARTPARK-IISc/Vaani", district, split="train", num_proc=20,
                      token=HF_TOKEN, cache_dir=cache_dir, streaming=False)
ds = ds.cast_column("audio", datasets.Audio(decode=False))
ds

Resolving data files:   0%|          | 0/57 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/54 [00:00<?, ?it/s]

Loading dataset shards:   0%|          | 0/54 [00:00<?, ?it/s]

Dataset({
    features: ['audio', 'language', 'languagesKnown', 'gender', 'state', 'district', 'pincode', 'stay(years)', 'isTranscriptionAvailable', 'transcript', 'referenceImage'],
    num_rows: 164125
})

In [3]:
from tqdm import tqdm
import polars as pl

# Initialize empty containers
audio_paths = []
columns = {col: [] for col in ds.column_names if col != "audio"}

# Iterate with tqdm
for row in tqdm(ds, desc="Processing rows", ncols=70, colour='green'):
    audio_paths.append(row["audio"]["path"])
    for col in columns:
        columns[col].append(row[col])

# Combine into Polars DataFrame
df = pl.DataFrame({
    "audio_path": audio_paths,
    **columns
})

Processing rows: 100%|██████| 164125/164125 [00:30<00:00, 5299.76it/s]


In [4]:
df

shape: (164_125, 11)
┌────────────┬──────────┬────────────┬────────┬───┬────────────┬───────────┬───────────┬───────────┐
│ audio_path ┆ language ┆ languagesK ┆ gender ┆ … ┆ stay(years ┆ isTranscr ┆ transcrip ┆ reference │
│ ---        ┆ ---      ┆ nown       ┆ ---    ┆   ┆ )          ┆ iptionAva ┆ t         ┆ Image     │
│ str        ┆ str      ┆ ---        ┆ str    ┆   ┆ ---        ┆ ilable    ┆ ---       ┆ ---       │
│            ┆          ┆ str        ┆        ┆   ┆ str        ┆ ---       ┆ str       ┆ str       │
│            ┆          ┆            ┆        ┆   ┆            ┆ str       ┆           ┆           │
╞════════════╪══════════╪════════════╪════════╪═══╪════════════╪═══════════╪═══════════╪═══════════╡
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Female ┆ … ┆ NewDelhi(2 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 0)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_GE │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ NER…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Female ┆ … ┆ NewDelhi(1 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 9)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_GE │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ NER…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Female ┆ … ┆ NewDelhi(1 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 1)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_Ne │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ wDe…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Male   ┆ … ┆ NewDelhi(2 ┆ Yes       ┆ ऐच_डी_ऐफ_ ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 4)         ┆           ┆ सी बैंक     ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆ {H_D_F_C  ┆ roject_GE │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆ bank…     ┆ NER…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Male   ┆ … ┆ NewDelhi(2 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 0)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_GE │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ NER…      │
│ …          ┆ …        ┆ …          ┆ …      ┆ … ┆ …          ┆ …         ┆ …         ┆ …         │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Male   ┆ … ┆ NewDelhi(4 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 5)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_Ne │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ wDe…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Female ┆ … ┆ CentralDel ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ hi(31)     ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_Ne │
│ …          ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ wDe…      │
│ IISc_Vaani ┆ Hindi    ┆ ['Hindi']  ┆ Female ┆ … ┆ NewDelhi(2 ┆ No        ┆ null      ┆ Images/II │
│ Project_M_ ┆          ┆            ┆        ┆   ┆ 0)         ┆           ┆           ┆ Sc_VaaniP │
│ Delhi_NewD ┆          ┆            ┆        ┆   ┆            ┆           ┆           ┆ roject_Ne │
│ …          ┆          ┆            ┆

In [12]:
cache_dir

'/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/Audio-Cache/Hindi/Delhi_NewDelhi'

In [6]:
def walkDIR(folder_path, include=None):
    file_list = []
    for root, _, files in os.walk(folder_path):
        for file in files:
            if include is None or any(file.endswith(ext) for ext in include):
                file_list.append(os.path.join(root, file))
    print("Files found:", len(file_list))
    return file_list

shards = walkDIR(cache_dir, include=['.arrow'])

Files found: 54


In [18]:
shards[0]

'/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/Audio-Cache/Hindi/Delhi_NewDelhi/ARTPARK-IISc___vaani/Delhi_NewDelhi/0.0.0/bebdc89de129c988e87623d031860f3abdb77ac5/vaani-train-00011-of-00054.arrow'

In [ ]:
'/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/Audio-Cache/Hindi/Delhi_NewDelhi/ARTPARK-IISc___vaani/Delhi_NewDelhi/0.0.0'

In [11]:
shards[0]

'/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/Audio-Cache/Hindi/Delhi_NewDelhi/ARTPARK-IISc___vaani/Delhi_NewDelhi/0.0.0/bebdc89de129c988e87623d031860f3abdb77ac5/vaani-train-00011-of-00054.arrow'

In [ ]:
from datasets import load_dataset, Audio
import polars as pl
import os
from tqdm import tqdm

def make_filter_df_from_hf(state, district, cache_dir, savedir, hf_token=None):
    # Load dataset
    ds = load_dataset(
        "ARTPARK-IISc/Vaani",
        district,
        split="train",
        num_proc=20,
        token=hf_token,
        cache_dir=cache_dir,
        streaming=False
    )

    # Cast audio column to keep path only (no decoding)
    ds = ds.cast_column("audio", Audio(decode=False))

    # Initialize empty containers
    audio_paths = []
    columns = {col: [] for col in ds.column_names if col != "audio"}

    # Iterate with tqdm
    for row in tqdm(ds, desc=f"Processing {state}_{district}"):
        audio_paths.append(row["audio"]["path"])
        for col in columns:
            columns[col].append(row[col])

    # Combine into Polars DataFrame
    df = pl.DataFrame({
        "audio_path": audio_paths,
        **columns
    })

    # Save as Parquet
    os.makedirs(savedir, exist_ok=True)
    out_path = os.path.join(savedir, f"{state}_{district}_meta.parquet")
    df.write_parquet(out_path, compression="gzip")

    print(f"✅ Saved {state}_{district}_meta.parquet to {out_path}")


<hr>
<hr>

In [1]:
import os
from huggingface_hub import login

# HF_TOKEN = open("/home/IITB/ai-at-ieor/23m1521/.cache/huggingface/token", "r").read().strip()
# os.environ["HF_TOKEN"] = HF_TOKEN
# login(token=HF_TOKEN)

In [2]:
# from datasets import get_dataset_config_names
# configs = get_dataset_config_names("ARTPARK-IISc/Vaani")

configs = ['AndhraPradesh_Anantpur', 'AndhraPradesh_Chittoor', 'AndhraPradesh_Guntur', 'AndhraPradesh_Krishna', 'AndhraPradesh_Srikakulam', 'AndhraPradesh_Vishakapattanam', 'ArunachalPradesh_Longding', 'ArunachalPradesh_PapumPare', 'Assam_KamrupMetropolitan', 'Assam_Sonitpur', 'Bihar_Araria', 'Bihar_Begusarai', 'Bihar_Bhagalpur', 'Bihar_Darbhanga', 'Bihar_EastChamparan', 'Bihar_Gaya', 'Bihar_Gopalganj', 'Bihar_Jahanabad', 'Bihar_Jamui', 'Bihar_Kaimur', 'Bihar_Katihar', 'Bihar_Kishanganj', 'Bihar_Lakhisarai', 'Bihar_Madhepura', 'Bihar_Muzaffarpur', 'Bihar_Patna', 'Bihar_Purnia', 'Bihar_Saharsa', 'Bihar_Samastipur', 'Bihar_Saran', 'Bihar_Sitamarhi', 'Bihar_Supaul', 'Bihar_Vaishali', 'Bihar_WestChamparan', 'Chandigarh_Chandigarh', 'Chhattisgarh_Balrampur', 'Chhattisgarh_Bastar', 'Chhattisgarh_Bilaspur', 'Chhattisgarh_Jashpur', 'Chhattisgarh_Kabirdham', 'Chhattisgarh_Korba', 'Chhattisgarh_Raigarh', 'Chhattisgarh_Rajnandgaon', 'Chhattisgarh_Sarguja', 'Chhattisgarh_Sukma', 'Delhi_NewDelhi', 'Goa_NorthSouthGoa', 'Jharkhand_Deoghar', 'Jharkhand_Garhwa', 'Jharkhand_Jamtara', 'Jharkhand_Palamu', 'Jharkhand_Ranchi', 'Jharkhand_Sahebganj', 'Karnataka_Bangalore', 'Karnataka_Belgaum', 'Karnataka_Bellary', 'Karnataka_Bidar', 'Karnataka_Bijapur', 'Karnataka_Chamrajnagar', 'Karnataka_DakshinKannada', 'Karnataka_Dharwad', 'Karnataka_Gulbarga', 'Karnataka_Koppal', 'Karnataka_Mysore', 'Karnataka_Raichur', 'Karnataka_Shimoga', 'MadhyaPradesh_Bhopal', 'MadhyaPradesh_Dhar', 'MadhyaPradesh_Katni', 'Maharashtra_Aurangabad', 'Maharashtra_Chandrapur', 'Maharashtra_Dhule', 'Maharashtra_Nagpur', 'Maharashtra_Pune', 'Maharashtra_Sindhudurga', 'Maharashtra_Solapur', 'Meghalaya_WestGaroHills', 'Nagaland_Dimapur', 'Nagaland_Kohima', 'Odisha_Khordha', 'Rajasthan_Churu', 'Rajasthan_Jaipur', 'Rajasthan_Nagaur', 'TamilNadu_Chennai', 'TamilNadu_Kanyakumari', 'TamilNadu_Namakkal', 'TamilNadu_Nilgiris', 'Telangana_Hyderabad', 'Telangana_Karimnagar', 'Telangana_Mahabubabad', 'Telangana_Nalgonda', 'Tripura_Dhalai', 'Tripura_Unakoti', 'Tripura_WestTripura', 'UttarPradesh_Budaun', 'UttarPradesh_Deoria', 'UttarPradesh_Etah', 'UttarPradesh_Ghazipur', 'UttarPradesh_Gorakhpur', 'UttarPradesh_Hamirpur', 'UttarPradesh_Jalaun', 'UttarPradesh_JyotibaPhuleNagar', 'UttarPradesh_Lalitpur', 'UttarPradesh_Lucknow', 'UttarPradesh_Muzzaffarnagar', 'UttarPradesh_Saharanpur', 'UttarPradesh_Varanasi', 'Uttarakhand_TehriGarhwal', 'Uttarakhand_Uttarkashi', 'WestBengal_Alipurduar', 'WestBengal_CoochBehar', 'WestBengal_DakshinDinajpur', 'WestBengal_Darjeeling', 'WestBengal_Jalpaiguri', 'WestBengal_Jhargram', 'WestBengal_Kolkata', 'WestBengal_Malda', 'WestBengal_North24Parganas', 'WestBengal_PaschimMedinipur', 'WestBengal_Purulia', 'images']
print(configs, "\n\n")

['AndhraPradesh_Anantpur', 'AndhraPradesh_Chittoor', 'AndhraPradesh_Guntur', 'AndhraPradesh_Krishna', 'AndhraPradesh_Srikakulam', 'AndhraPradesh_Vishakapattanam', 'ArunachalPradesh_Longding', 'ArunachalPradesh_PapumPare', 'Assam_KamrupMetropolitan', 'Assam_Sonitpur', 'Bihar_Araria', 'Bihar_Begusarai', 'Bihar_Bhagalpur', 'Bihar_Darbhanga', 'Bihar_EastChamparan', 'Bihar_Gaya', 'Bihar_Gopalganj', 'Bihar_Jahanabad', 'Bihar_Jamui', 'Bihar_Kaimur', 'Bihar_Katihar', 'Bihar_Kishanganj', 'Bihar_Lakhisarai', 'Bihar_Madhepura', 'Bihar_Muzaffarpur', 'Bihar_Patna', 'Bihar_Purnia', 'Bihar_Saharsa', 'Bihar_Samastipur', 'Bihar_Saran', 'Bihar_Sitamarhi', 'Bihar_Supaul', 'Bihar_Vaishali', 'Bihar_WestChamparan', 'Chandigarh_Chandigarh', 'Chhattisgarh_Balrampur', 'Chhattisgarh_Bastar', 'Chhattisgarh_Bilaspur', 'Chhattisgarh_Jashpur', 'Chhattisgarh_Kabirdham', 'Chhattisgarh_Korba', 'Chhattisgarh_Raigarh', 'Chhattisgarh_Rajnandgaon', 'Chhattisgarh_Sarguja', 'Chhattisgarh_Sukma', 'Delhi_NewDelhi', 'Goa_North

In [4]:
import pandas as pd
urls_dict = {'state': [], 'district': [], 'url': [], 'config_name':[]}

for i in configs:
    state = i.split('_')[0]
    district = i.split('_')[-1]
    urls_dict['state'].append(state)
    urls_dict['district'].append(district)
    urls_dict['url'].append(f"hf://datasets/ARTPARK-IISc/Vaani/audio/{state}/{district}/train-*.parquet")
    urls_dict['config_name'].append(i)

urls_df = pd.DataFrame(urls_dict)
urls_df

state          district  \
0    AndhraPradesh          Anantpur   
1    AndhraPradesh          Chittoor   
2    AndhraPradesh            Guntur   
3    AndhraPradesh           Krishna   
4    AndhraPradesh        Srikakulam   
..             ...               ...   
116     WestBengal             Malda   
117     WestBengal   North24Parganas   
118     WestBengal  PaschimMedinipur   
119     WestBengal           Purulia   
120         images            images   

                                                   url  \
0    hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraP...   
1    hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraP...   
2    hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraP...   
3    hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraP...   
4    hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraP...   
..                                                 ...   
116  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
117  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
118  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
119  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
120  hf://datasets/ARTPARK-IISc/Vaani/audio/images/...   

                     config_name  
0         AndhraPradesh_Anantpur  
1         AndhraPradesh_Chittoor  
2           AndhraPradesh_Guntur  
3          AndhraPradesh_Krishna  
4       AndhraPradesh_Srikakulam  
..                           ...  
116             WestBengal_Malda  
117   WestBengal_North24Parganas  
118  WestBengal_PaschimMedinipur  
119           WestBengal_Purulia  
120                       images  

[121 rows x 4 columns]

In [5]:
urls_df.iloc[11:,:]

state          district  \
11        Bihar         Begusarai   
12        Bihar         Bhagalpur   
13        Bihar         Darbhanga   
14        Bihar     EastChamparan   
15        Bihar              Gaya   
..          ...               ...   
116  WestBengal             Malda   
117  WestBengal   North24Parganas   
118  WestBengal  PaschimMedinipur   
119  WestBengal           Purulia   
120      images            images   

                                                   url  \
11   hf://datasets/ARTPARK-IISc/Vaani/audio/Bihar/B...   
12   hf://datasets/ARTPARK-IISc/Vaani/audio/Bihar/B...   
13   hf://datasets/ARTPARK-IISc/Vaani/audio/Bihar/D...   
14   hf://datasets/ARTPARK-IISc/Vaani/audio/Bihar/E...   
15   hf://datasets/ARTPARK-IISc/Vaani/audio/Bihar/G...   
..                                                 ...   
116  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
117  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
118  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
119  hf://datasets/ARTPARK-IISc/Vaani/audio/WestBen...   
120  hf://datasets/ARTPARK-IISc/Vaani/audio/images/...   

                     config_name  
11               Bihar_Begusarai  
12               Bihar_Bhagalpur  
13               Bihar_Darbhanga  
14           Bihar_EastChamparan  
15                    Bihar_Gaya  
..                           ...  
116             WestBengal_Malda  
117   WestBengal_North24Parganas  
118  WestBengal_PaschimMedinipur  
119           WestBengal_Purulia  
120                       images  

[110 rows x 4 columns]

In [6]:
!du -sh /home/IITB/ai-at-ieor/23m1521/.cache/huggingface/hub/.locks/datasets--ARTPARK-IISc--Vaani

144K	/home/IITB/ai-at-ieor/23m1521/.cache/huggingface/hub/.locks/datasets--ARTPARK-IISc--Vaani


In [6]:
import polars as pl
from tqdm import tqdm, trange
import os

def make_filter_df(state, district, url, savedir):
    df = pl.scan_parquet(url).with_columns(
        pl.col('audio').struct.field('path').alias('audio_path')
        ).drop('audio').collect(
            ).write_parquet(
                f"{savedir}/{state}_{district}_meta.parquet",
                compression="gzip"
                )
    print(f"✅ Saved {state}_{district}_meta.parquet")
    
savedir = "/scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData"
os.makedirs(savedir, exist_ok=True)

for row in tqdm(urls_df.iterrows(), total=len(urls_df), colour='yellow', ncols=70):
    state = row[1]['state']
    district = row[1]['district']
    url = row[1]['url']
    print(state, district, url, savedir)

100%|████████████████████████████| 121/121 [00:00<00:00, 21100.56it/s]

AndhraPradesh Anantpur hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Anantpur/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
AndhraPradesh Chittoor hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Chittoor/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
AndhraPradesh Guntur hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Guntur/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
AndhraPradesh Krishna hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Krishna/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
AndhraPradesh Srikakulam hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Srikakulam/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
AndhraPradesh Vishakapattanam hf://datasets/ARTPARK-IISc/Vaani/audio/AndhraPradesh/Vishakapattanam/train-*.parquet /scratch/IITB/ai-at-ieor/23m1521/datasets/Vaani/MetaData
ArunachalPradesh Longding hf://datasets/

In [15]:
done = ["_".join(i.split(".")[:-1][0].split("_")[:-1]) for i in sorted(os.listdir(savedir))]
done

['AndhraPradesh_Anantpur',
 'AndhraPradesh_Chittoor',
 'AndhraPradesh_Guntur',
 'AndhraPradesh_Krishna',
 'AndhraPradesh_Srikakulam',
 'ArunachalPradesh_Longding',
 'ArunachalPradesh_PapumPare',
 'Assam_KamrupMetropolitan',
 'Assam_Sonitpur',
 'Bihar_Araria']